<link rel="stylesheet" href="../../styles/theme_style.css">
<!--link rel="stylesheet" href="../../styles/header_style.css"-->
<link rel="stylesheet" href="https://cdnjs.cloudflare.com/ajax/libs/font-awesome/4.7.0/css/font-awesome.min.css">

<table width="100%">
    <tr>
        <td id="image_td" width="15%" class="header_image_color_4"><div id="image_img" class="header_image_4"></div></td>
        <!-- Available classes for "image_td" element:
        - header_image_color_1 (For Notebooks of "Open" Area);
        - header_image_color_2 (For Notebooks of "Acquire" Area);
        - header_image_color_3 (For Notebooks of "Visualise" Area);
        - header_image_color_4 (For Notebooks of "Process" Area);
        - header_image_color_5 (For Notebooks of "Detect" Area);
        - header_image_color_6 (For Notebooks of "Extract" Area);
        - header_image_color_7 (For Notebooks of "Decide" Area);
        - header_image_color_8 (For Notebooks of "Explain" Area);

        Available classes for "image_img" element:
        - header_image_1 (For Notebooks of "Open" Area);
        - header_image_2 (For Notebooks of "Acquire" Area);
        - header_image_3 (For Notebooks of "Visualise" Area);
        - header_image_4 (For Notebooks of "Process" Area);
        - header_image_5 (For Notebooks of "Detect" Area);
        - header_image_6 (For Notebooks of "Extract" Area);
        - header_image_7 (For Notebooks of "Decide" Area);
        - header_image_8 (For Notebooks of "Explain" Area);-->
        <td class="header_text"> Digital Filtering - A Fundamental Pre-Processing Step </td>
    </tr>
</table>

<div id="flex-container">
    <div id="diff_level" class="flex-item">
        **Difficulty Level:**   <span class="fa fa-star checked"></span>
                                <span class="fa fa-star checked"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
                                <span class="fa fa-star"></span>
    </div>
    <div id="tag" class="flex-item-tag">
        <span id="tag_list">
            <table id="tag_list_table">
                <tr>
                    <td class="shield_left">Tags</td>
                    <td class="shield_right" id="tags">process|filters</td> 
                </tr>
            </table>
        </span>
        <!-- [OR] Visit https://img.shields.io in order to create a tag badge-->
    </div>
</div>

The acquired electrophysiological signals have always two intrinsic components.
The signal we really want to acquire and study and noise, i.e. the acquisition component that is not relevant for the study purposes.

Noise can have different origins, such as in random events or due to voluntary/involuntary movements of the subject under analysis that affect the signal acquisition.

So, filtering is a fundamental step that needs to be applied to the signal, in order to ensure the maximisation of signal to noise ratio. Filtering can be achieved by hardware, having the analogical systems a great relevance, or by software using digital filters.

In this **<span class="color5">Jupyter Notebook</span>** it will be demonstrated how to digital filter the signal.

<hr>

<p class="steps">1 - Importation of the needed packages</p>

In [1]:
# OpenSignals Tools own package for loading and plotting the acquired data
import opensignalstools.open as ostOpen
import opensignalstools.visualise as ostVis

# Scientific package
import numpy

# Signal Processing package where digital filtering functions are included
from novainstrumentation.tools import plotfft
from novainstrumentation.filter import bandpass
from novainstrumentation.freq_analysis import max_frequency

# Base packages used in OpenSignals Tools Notebooks for plotting data
from bokeh.plotting import figure, output_file, show
from bokeh.io import output_notebook
from bokeh.layouts import gridplot
from bokeh.models import BoxAnnotation, Arrow, VeeHead
from bokeh.models.tools import *
output_notebook(hide_banner=True)

<p class="steps">2 - Load of acquired ECG data</p>

In [2]:
# Load of data
data, header = ostOpen.loadData("../Open/signals/ecg_4000_Hz.h5", getHeader=True)

<p class="steps">3 - Identification of mac address of the device and the channel used during acquisition</p>

In [3]:
mac_address = list(data.keys())[0]
channel = list(data[mac_address].keys())[0]

print ("Mac Address: " + str(mac_address) + " Channel: " + str(channel))

Mac Address: 00:07:80:D8:A7:F9 Channel: CH1


<p class="steps">3 - Generation of signal power spectrum by *Fast Fourier Transform* (FFT)</p>
*With this step is possible to observe the frequency composition of ECG signal.*

In [4]:
# Sampling frequency of the acquisition
fs = header[mac_address]["sampling rate"]

# Acquired data
signal = data[mac_address][channel]

# Power spectrum
freq_axis_1, power_spect_1 = plotfft(signal, fs)

<p class="steps">4 - The informational content of ECG signal is typically contained inside the frequency band [0.5, 40] Hz</p>
*With the next representation we can conclude that exist some unwanted information out of this frequency band.*

In [5]:
# List that store the figure handler
list_figures_1 = []

# Plotting of power spectrum  
list_figures_1.append(figure(x_axis_label='Frequency (Hz)', y_axis_label='Relative Weight', **ostVis.opensignalsKwargs("figure"), x_range=(0, 100), y_range=(0, 5e6)))
list_figures_1[-1].line(freq_axis_1, power_spect_1, legend="ECG Power Spectrum", **ostVis.opensignalsKwargs("line"))

# Highlighting of information band
color = ostVis.opensignalsColorPallet()
box_annotation = BoxAnnotation(left=0.5, right=40, fill_color=color, fill_alpha=0.1)
list_figures_1[-1].circle([-100], [0], fill_color=color,  fill_alpha=0.1, legend="Informational Band")
list_figures_1[-1].add_layout(box_annotation)

In [22]:
show(list_figures_1[-1])

<p class="steps">5 - Application of a pass-band filter in order to be excluded the unwanted information out of [0.5, 40] Hz frequency band</p>

In [7]:
# Digital filtering with a low cutoff frequency f1 of 0.5 Hz and high cutoff frequency f2 of 40 Hz
filter_signal_1 = bandpass(signal, f1=0.5, f2=40, order=1, fs=fs, use_filtfilt=True)

# Power spectrum
freq_axis_2, power_spect_2 = plotfft(filter_signal_1, fs)

<p class="steps">6 - Comparison of the power spectrum of original and filtered signal</p>

In [8]:
# List that store the figure handler
list_figures_2 = [[]]

# Copy of the figure of the original signal power spectrum
list_figures_2[-1].append(list_figures_1[-1])

# Plotting of filtered signal power spectrum    
list_figures_2[-1].append(figure(x_axis_label='Frequency (Hz)', y_axis_label='Relative Weight', **ostVis.opensignalsKwargs("figure"), x_range=(0, 100), y_range=(0, 5e6)))
list_figures_2[-1][-1].line(freq_axis_2, power_spect_2, legend="Filtered FFT (Order 1)", **ostVis.opensignalsKwargs("line"))

# Highlighting of information band
color = ostVis.opensignalsColorPallet()
box_annotation = BoxAnnotation(left=0.5, right=40, fill_color=color, fill_alpha=0.1)
list_figures_2[-1][-1].circle([-100], [0], fill_color=color,  fill_alpha=0.1, legend="Informational Band")
list_figures_2[-1][-1].add_layout(box_annotation)

In [23]:
grid_plot_1 = gridplot(list_figures_2, **ostVis.opensignalsKwargs("gridplot"))
show(grid_plot_1)

In this first filtering attempt we used a first order filter (input argument order=1). It can be seen, in the previous figure, that some unwanted information have been removed, unfortunately no filter has an ideal behaviour, so despite we specify a high cutoff frequency of 40 Hz, some information above this threshold is mantained after filtering.

The good news are that components greater than 80 Hz are almost completely removed.

The filter performance can be improved by increasing the filter order, because the higher the filter order is, more quickly the transition between the pass and stop band will be (the transition band will be smaller).
<a href="https://www.ecnmag.com/article/2016/05/practical-filter-design-challenges-and-considerations-precision-adcs"><img src="../../images/process/butterworth_filter.png" width="50%"></a>

<p class="steps">7 - Repetition of the filtering stage but using a higher filter order</p>

In [10]:
# Digital filtering with a low cutoff frequency f1 of 0.5 Hz and high cutoff frequency f2 of 40 Hz
filter_signal_2 = bandpass(signal, f1=0.5, f2=40, order=3, fs=fs, use_filtfilt=True)

# Power spectrum
freq_axis_3, power_spect_3 = plotfft(filter_signal_2, fs)

In [11]:
# List that store the figure handler
list_figures_3 = [[]]

# Copy of the figure of the original and first order filtered signal power spectrum
list_figures_3[-1].append(list_figures_1[-1])
list_figures_3.append([])
list_figures_3[-1].append(list_figures_2[-1][-1])
list_figures_3.append([])

# Plotting of filtered signal power spectrum    
list_figures_3[-1].append(figure(x_axis_label='Frequency (Hz)', y_axis_label='Relative Weight', **ostVis.opensignalsKwargs("figure"), x_range=(0, 100), y_range=(0, 5e6)))
list_figures_3[-1][-1].line(freq_axis_3, power_spect_3, legend="Filtered ECG Power Spectrum (Order 3)", **ostVis.opensignalsKwargs("line"))

# Highlighting of information band
color = ostVis.opensignalsColorPallet()
box_annotation = BoxAnnotation(left=0.5, right=40, fill_color=color, fill_alpha=0.1)
list_figures_3[-1][-1].circle([-100], [0], fill_color=color,  fill_alpha=0.1, legend="Informational Band")
list_figures_3[-1][-1].add_layout(box_annotation)

In [12]:
# Determination of the maximum frequency
max_freq_1 = max_frequency(signal, fs)
max_freq_2 = max_frequency(filter_signal_1, fs)
max_freq_3 = max_frequency(filter_signal_2, fs)

box_annotations = []
for iter_nbr, max_freq in enumerate([max_freq_1, max_freq_2, max_freq_3]):
    # Rejection band (above maximum frequency)
    color = "black"
    box_annotations.append(BoxAnnotation(left=max_freq, right=max_freq + 5, fill_color=color, fill_alpha=0.1))
    
    # Show of the plots with the rejection band
    list_figures_3[-3 + iter_nbr][0].circle([-100], [0], fill_color=color,  fill_alpha=0.1, legend="Rejected Band")
    list_figures_3[-3 + iter_nbr][0].add_layout(box_annotations[-1])
    list_figures_3[-3 + iter_nbr][0].add_layout(Arrow(end=VeeHead(size=15, line_color=color, fill_color=color, fill_alpha=0.1), line_color=color, x_start=max_freq + 5, y_start=2.5e6, x_end=max_freq + 15, y_end=2.5e6))

In [24]:
grid_plot_2 = gridplot(list_figures_3, **ostVis.opensignalsKwargs("gridplot"))
show(grid_plot_2)

When the noise level is low, it may be difficult to observe its influence in time domain.
In order to the digital filtering stage produce a visual effect in time domain, the noise level needs to be high.

So we will add some artifitial noise do the signal and see the great impact of digital filtering.

<hr>

<p class="steps">E1 - Addition of artificial noise</p>

In [14]:
# Noise samples and translation of the baseline 
baseline = numpy.average(signal)
baseline_shift = 0.50 * baseline
noisy_signal = signal + numpy.random.normal(0, 1000, len(signal)) + baseline_shift

<p class="steps">E2 - Noisy signal representation</p>

In [15]:
# List that store the figure handler
list_figures_4 = []

# Plotting of power spectrum    
list_figures_4.append(figure(x_axis_label='Sample Number', y_axis_label='Raw Data', title="Noisy Signal", y_range=(-1e4, 6e4), **ostVis.opensignalsKwargs("figure")))
list_figures_4[-1].line(numpy.linspace(0, len(noisy_signal) - 1, len(noisy_signal)), noisy_signal, **ostVis.opensignalsKwargs("line"))

GlyphRenderer(id='f2912f12-f4cf-46c0-9ad1-8e59b021e624', ...)

In [25]:
show(list_figures_4[-1])

<p class="steps">E3 - Digital Filtering Stage</p>

In [17]:
# Digital filtering with a low cutoff frequency f1 of 0.5 Hz and high cutoff frequency f2 of 40 Hz
noisy_signal_filter = bandpass(noisy_signal, f1=0.5, f2=40, order=3, fs=fs, use_filtfilt=True)

<p class="steps">E4 - Comparison of noisy and filtered signal in time domain</p>

In [18]:
# List that store the figure handler
list_figures_5 = [[]]

# Copy of the previous figure
list_figures_5[-1].append(list_figures_4[-1])

# Plotting of power spectrum    
list_figures_5[-1].append(figure(x_axis_label='Sample Number', y_axis_label='Raw Data', title="Filtered Signal", y_range=(-1e4, 6e4), **ostVis.opensignalsKwargs("figure")))
list_figures_5[-1][-1].line(numpy.linspace(0, len(noisy_signal_filter) - 1, len(noisy_signal_filter)), noisy_signal_filter, **ostVis.opensignalsKwargs("line"))


GlyphRenderer(id='ccfa7725-d173-41b8-8a38-85e35a351800', ...)

In [26]:
grid_plot_3 = gridplot(list_figures_5, **ostVis.opensignalsKwargs("gridplot"))
show(grid_plot_3)

<span class="color6">**Auxiliary Code Segment (should not be replicated by the user)**</span>

In [20]:
from IPython.display import Javascript
ostVis.opensignalsStyle(list_figures_1)
ostVis.opensignalsStyle([item for sublist in list_figures_2 for item in sublist])
ostVis.opensignalsStyle([item for sublist in list_figures_3 for item in sublist])
ostVis.opensignalsStyle(list_figures_4)
ostVis.opensignalsStyle([item for sublist in list_figures_5 for item in sublist])
Javascript("Jupyter.notebook.execute_cells([14, 19, 25, 32, 37])")

<IPython.core.display.Javascript object>

In [21]:
from opensignalstools.__notebook_support__ import cssStyleApply
cssStyleApply()

.................... CSS Style Applied to Jupyter Notebook .........................
